In [1]:
# Import libraries

import folium
from folium.plugins import Geocoder
import geopandas as gpd

In [2]:
# Read traffic site geojson file
traffic_site_gdf = gpd.read_file("../data/traffic_sites.geojson")

# Create map
map = folium.Map(
    location=[traffic_site_gdf.geometry.y.mean(), traffic_site_gdf.geometry.x.mean()],
    tiles="OpenStreetMap"
)

# Create traffic sites on map
for row in traffic_site_gdf.itertuples():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=4,
        tooltip=f"Site Number: {row.SITE_NO}, Site Name: {row.SITE_NAME}"
    ).add_to(map)

# Add location search bar 
Geocoder().add_to(map)

map

In [3]:
# Create suburb column

# Read suburbs shapefile
suburbs_shp = gpd.read_file(f"../data/suburbs.zip")
suburbs_shp = suburbs_shp.to_crs("EPSG: 4326")

# Find which suburb each site is located in
traffic_site_gdf = gpd.sjoin(traffic_site_gdf, suburbs_shp[["SAL_NAME21", "geometry"]], how='left', predicate='within')

# Rename column names
traffic_site_gdf.rename(columns={"SITE_NO": "site_id", "SITE_NAME": "site_name", "SAL_NAME21": "suburb"}, inplace=True)

# Remove (Vic. ) from end of suburb strings
traffic_site_gdf["suburb"] = (traffic_site_gdf["suburb"].str.replace(r"\s*\(Vic\.\)$", "", regex=True))

# Sort by suburb and site_id
traffic_site_gdf.sort_values(by=["suburb", "site_id"], inplace=True)

# Save DataFrame
traffic_site_gdf[["site_id", "site_name", "suburb"]].to_csv("../data/traffic_site_info.csv", index=False)

traffic_site_gdf[["site_id", "site_name", "suburb"]]

site_id                            site_name      suburb
4285     1489                       HODDLE / ABBOT  Abbotsford
37       2458  JOHNSTON O/H LANE E HODDLE GANTRY 8  Abbotsford
38       2459    JOHNSTON O/H LANE W PARK GANTRY 9  Abbotsford
39       2460   JOHNSTON O/H LANE E PARK GANTRY 10  Abbotsford
40       2461   JOHNSTON O/H LANE E RICH GANTRY 11  Abbotsford
...       ...                                  ...         ...
2789     4254                      FRANCIS/WEMBLEY  Yarraville
2790     4255                      FRANCIS/STEPHEN  Yarraville
2951     4257                WILLIAMSTOWN/ANDERSON  Yarraville
2952     4258               WILLIAMSTOWN NR CASTLE  Yarraville
3404     6102              BELMORE BTW ORR & PIPER  Yarrawonga

[4852 rows x 3 columns]